In [1]:
%pip install cassandra-driver
%pip install pandas


Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [2]:
import pandas as pd

data = pd.read_csv("/home/olha/olha-de-internship/_nosql/Student Depression Dataset.csv")
print(data.dtypes)


id                                         int64
Gender                                    object
Age                                      float64
City                                      object
Profession                                object
Academic Pressure                        float64
Work Pressure                            float64
CGPA                                     float64
Study Satisfaction                       float64
Job Satisfaction                         float64
Sleep Duration                            object
Dietary Habits                            object
Degree                                    object
Have you ever had suicidal thoughts ?     object
Work/Study Hours                         float64
Financial Stress                         float64
Family History of Mental Illness          object
Depression                                 int64
dtype: object


In [3]:
from cassandra.cluster import Cluster
from cassandra.auth import PlainTextAuthProvider
auth_provider = PlainTextAuthProvider(username='admin', password='admin')
cluster = Cluster(['localhost'], port=9042, auth_provider=auth_provider)
session = cluster.connect()

def find_keyspaces():
    key_spaces = session.execute('DESC KEYSPACES')
    for key_space in key_spaces:
        print(key_space)
        
find_keyspaces()        

Row(keyspace_name='studentdeprsn', type='keyspace', name='studentdeprsn')
Row(keyspace_name='system', type='keyspace', name='system')
Row(keyspace_name='system_auth', type='keyspace', name='system_auth')
Row(keyspace_name='system_distributed', type='keyspace', name='system_distributed')
Row(keyspace_name='system_schema', type='keyspace', name='system_schema')
Row(keyspace_name='system_traces', type='keyspace', name='system_traces')
Row(keyspace_name='system_views', type='keyspace', name='system_views')
Row(keyspace_name='system_virtual_schema', type='keyspace', name='system_virtual_schema')


In [4]:
create_keyspace_query = '''
    CREATE KEYSPACE studentdeprsn WITH REPLICATION = {'class' : 'SimpleStrategy','replication_factor' : 1};
'''

session.execute(create_keyspace_query)

find_keyspaces()

AlreadyExists: Keyspace 'studentdeprsn' already exists

In [5]:
session.execute('USE studentdeprsn')


In [ ]:
create_table_query = '''
CREATE TABLE student_depression (
    city text,
    gender text,
    id int,
    age int,
    gpa float,
    sleep_duration int,
    profession text,
    work_pressure int,
    academic_pressure int,
    study_satisfaction int,
    job_satisfaction int,
    dietary_habits text,
    loaded_at timestamp,
    PRIMARY KEY ((city, gender), id)
)
'''
session.execute(create_table_query)


for table in session.execute('DESC TABLES'):
    print(table)

In [ ]:
from datetime import datetime
insert_query = '''
    INSERT INTO student_depression (city, gender, id, age, gpa, sleep_duration, profession,work_pressure,academic_pressure, study_satisfaction, job_satisfaction, dieatary_habits, loaded_at )
    VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
'''

for _, row in data.iterrows():
    session.execute(insert_query, (
        row['City'],                 
        row['Gender'],               
        row['id'],                
        row['Age'],
        row['CGPA'],
        row["Sleep Duration"],
        row['Profession'],
        row["Work Pressure"],
        row["Academic Pressure"],
        row["Study Satisfaction"],
        row["Job Satisfaction"],
        row["Dietary Habits"],
        datetime.now()               
    ))

In [9]:

create_new_table_query = '''
    CREATE TABLE student_depression_new (
        id int PRIMARY KEY,
        gender text,
        age float,  
        city text,
        gpa float,
        sleep_duration text,
        profession text,
        work_pressure float,
        academic_pressure float,
        study_satisfaction float,
        job_satisfaction float,
        dietary_habits text,
        loaded_at timestamp
    )
    
'''
session.execute(create_new_table_query)

AlreadyExists: Table 'studentdeprsn.student_depression_new' already exists

In [11]:
from datetime import datetime


insert_data = '''
    INSERT INTO student_depression_new (
        id, gender, age, city, gpa, sleep_duration, profession, 
        work_pressure, academic_pressure, study_satisfaction, 
        job_satisfaction, dietary_habits, loaded_at
    )
    VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
'''

truncate_data = '''
    TRUNCATE TABLE student_depression_new
'''
session.execute(truncate_data)

for _, row in data.iterrows():
    session.execute(insert_data, (
        row['id'],
        row['Gender'],
        float(row['Age']),
        row['City'],
        float(row['CGPA']),
        row["Sleep Duration"],
        row['Profession'],
        float(row["Work Pressure"]),
        float(row["Academic Pressure"]),
        float(row["Study Satisfaction"]),
        float(row["Job Satisfaction"]),
        row["Dietary Habits"],
        datetime.now()  
    ))




### Read

In [12]:
def read_all_records(table_name):
    try:
        return session.execute("SELECT * FROM {}".format(table_name))
    except Exception as e:
        return "Read fails with " + e

def print_records(records):
    for record in records:
        print(record)

records = read_all_records('student_depression_new')

print_records(records)

Row(id=121478, academic_pressure=3.0, age=25.0, city='Srinagar', dietary_habits='Unhealthy', gender='Male', gpa=9.390000343322754, job_satisfaction=0.0, loaded_at=datetime.datetime(2024, 12, 16, 19, 12, 17, 317000), profession='Student', sleep_duration='7-8 hours', study_satisfaction=5.0, work_pressure=0.0)
Row(id=123410, academic_pressure=3.0, age=29.0, city='Hyderabad', dietary_habits='Unhealthy', gender='Male', gpa=9.539999961853027, job_satisfaction=0.0, loaded_at=datetime.datetime(2024, 12, 16, 19, 12, 17, 561000), profession='Student', sleep_duration='Less than 5 hours', study_satisfaction=4.0, work_pressure=0.0)
Row(id=91274, academic_pressure=4.0, age=25.0, city='Patna', dietary_habits='Unhealthy', gender='Female', gpa=8.25, job_satisfaction=0.0, loaded_at=datetime.datetime(2024, 12, 16, 19, 12, 13, 177000), profession='Student', sleep_duration='More than 8 hours', study_satisfaction=4.0, work_pressure=0.0)
Row(id=37032, academic_pressure=2.0, age=27.0, city='Vadodara', dietary

### Filter

In [13]:
def read_records_by_city(table_name, city):
    try:
        return session.execute("SELECT * FROM {} WHERE city='{}' ALLOW FILTERING".format(table_name, city))
    except Exception as e:
        return "Read fails with " + e

print_records(read_records_by_city('student_depression_new', 'Agra'))

Row(id=127129, academic_pressure=1.0, age=23.0, city='Agra', dietary_habits='Moderate', gender='Male', gpa=6.590000152587891, job_satisfaction=0.0, loaded_at=datetime.datetime(2024, 12, 16, 19, 12, 18, 28000), profession='Student', sleep_duration='Less than 5 hours', study_satisfaction=1.0, work_pressure=0.0)
Row(id=80494, academic_pressure=5.0, age=18.0, city='Agra', dietary_habits='Healthy', gender='Male', gpa=5.570000171661377, job_satisfaction=0.0, loaded_at=datetime.datetime(2024, 12, 16, 19, 12, 11, 785000), profession='Student', sleep_duration='Less than 5 hours', study_satisfaction=2.0, work_pressure=0.0)
Row(id=37711, academic_pressure=2.0, age=34.0, city='Agra', dietary_habits='Moderate', gender='Female', gpa=5.079999923706055, job_satisfaction=0.0, loaded_at=datetime.datetime(2024, 12, 16, 19, 12, 6, 116000), profession='Student', sleep_duration='Less than 5 hours', study_satisfaction=5.0, work_pressure=0.0)
Row(id=132979, academic_pressure=1.0, age=26.0, city='Agra', dietar

### Update

In [16]:
def update_record(table_name, id, updated_response_value):
    try:
        return session.execute("UPDATE {} SET age={} WHERE id={}".format(table_name, updated_response_value, id))
    except Exception as e:
        return f"UPDATE fails with: {str(e)}"

update_record('student_depression_new', '12888', '35')

### Delete

In [19]:
def delete_records_by_id(table_name, id):
    try:
        return session.execute("DELETE FROM {} WHERE id={}".format(table_name, id))
    except Exception as e:
        return f"DELETE fails with: {str(e)}"

delete_records_by_id('student_depression_new', '12888')